In [150]:
import joblib
import os
import itertools
import re
import unidecode
import string
import cmath

import numpy as np
import pandas as pd
from sklearn import metrics

from zipfile import ZipFile
from collections import defaultdict
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics import confusion_matrix
from sklearn.preprocessing import normalize
from tqdm import tqdm

import matplotlib.pyplot as plt
%matplotlib inline

In [124]:
def comp_cos_sim(hdv1, hdv2):
    return(cosine_similarity(hdv1.real, [hdv2.real]))

def jobsave(object_to_save, filename):
    joblib.dump(object_to_save, filename)

def jobload(filename):
    return joblib.load(filename)

def plot_confusion_matrix(cm, classes,
                          normalize=False,
                          title='Confusion matrix',
                          cmap=plt.cm.Blues,
                          x_label='True label',
                          y_label='Predicted label'
                         ):
    plt.imshow(cm, interpolation='nearest', cmap=cmap)
    plt.title(title)
    plt.colorbar()
    tick_marks = np.arange(len(classes))
    plt.xticks(tick_marks, classes, rotation=45)
    plt.yticks(tick_marks, classes)
    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
        print("Normalized confusion matrix")
    else:
        print('Confusion matrix, without normalization')
    print(cm)
    thresh = cm.max() / 2.
    for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        plt.text(j, i, cm[i, j],
                 horizontalalignment="center",
                 color="white" if cm[i, j] > thresh else "black")
    plt.tight_layout()
    plt.ylabel(x_label)
    plt.xlabel(y_label);
    
def measure_cosine_similarity(hdv1, hdv2):
    return(cosine_similarity([hdv1], [hdv2]))

In [235]:
def hermitian_product_measure_1(hdv1, hdv2):
    numerator = hdv1 @ np.asmatrix(hdv2).getH()
    denominator = np.linalg.norm(hdv1) * np.linalg.norm(hdv2)
    return np.squeeze(np.asarray(np.real(numerator / denominator)))


def hermitian_product_measure_2(hdv1, hdv2):
    numerator = hdv1 @ np.asmatrix(hdv2).getH()
    denominator = np.linalg.norm(hdv1) * np.linalg.norm(hdv2)
    return np.squeeze(np.array((numerator / denominator).real))

In [169]:
from scipy.spatial import distance

In [212]:
ress = []
for i in range(len(lang_blocks_nl)):
    ress.append(hermitian_product_measure_1(HD_array, lang_blocks_nl[i]).argmax())

In [213]:
ress_2 = []
for i in range(len(lang_blocks_nl)):
    ress_2.append(hermitian_product_measure_2(HD_array, lang_blocks_nl[i]).argmax())

In [240]:
ress_3 = []
for i in range(len(lang_blocks_nl)):
    ress_3.append(hermitian_product_measure_2(HD_array, normalize_comp_vect(lang_blocks_nl[i])).argmax())

In [214]:
ress.count(0)/len(ress)

0.916234601494088

In [215]:
ress_2.count(0)/len(ress_2)

0.916234601494088

In [241]:
ress_3.count(0)/len(ress_3)

0.9109385049225746

In [243]:
ress_3.count(0)

368256

In [234]:
hermitian_product_measure_2(HD_array[0], HD_array[3])

IndexError: too many indices for array

In [239]:
hermitian_product_measure_2(HD_array, normalize_comp_vect(lang_blocks_nl[0]))

array([0.0505582 , 0.03318592, 0.01955513, 0.01553229, 0.02070561,
       0.01854315, 0.03129306, 0.04497684, 0.01374695, 0.02650921,
       0.02765666, 0.03392757, 0.02699757, 0.01873864, 0.03211089,
       0.02433083, 0.02342671, 0.03913254, 0.0372153 , 0.02316941,
       0.03923094])

In [238]:
lang_blocks_nl[0]

array([-1.69861668e+00-8.15885346e+00j,  3.09999267e+00+2.18983708e+00j,
       -1.86447508e+00-1.87599874e+00j,  2.69999289e+00+1.19474066e+01j,
       -2.19010067e+00+2.00168117e+00j,  3.84040493e-01-3.01000879e+00j,
       -2.43836042e-02+3.61215012e+00j,  2.11178097e-01+7.58406587e+00j,
       -5.52176998e+00+9.07727330e-01j, -4.89233325e+00-1.04868134e+00j,
        1.25027412e+01+2.50983818e+00j, -4.28790936e+00-2.34242510e+00j,
        1.73778898e+00-5.64097091e+00j,  2.22051144e+00-3.36259009e+00j,
        5.78565415e+00-4.49486347e+00j, -4.97301807e+00-3.65393021e+00j,
        1.38907431e+00-1.26556539e+01j, -4.76572730e+00-2.88431342e+00j,
       -1.07293345e+01+9.31994800e-01j, -3.75686060e+00+2.90441519e+00j,
        2.58993224e+00-1.33207561e+00j, -6.05235592e+00-5.18973838e-01j,
        4.04595273e+00-9.26737413e+00j, -5.95971428e+00+4.28144950e+00j,
        6.67052513e-01-3.38621783e-01j,  2.32107218e+00-3.33360458e+00j,
        8.45660572e-02+1.89349421e+00j, -9.28888586

In [186]:
hermitian_product_measure_1(a, b )

array(-0.77477477)

In [205]:
hermitian_product_measure_2(HD_array, lang_blocks_nl[0]).argmax()

0

In [4]:
def normalize_comp_vect(vector):
    real = vector.real
    imag = vector.imag
    norm_factor = vector.real**2 + vector.imag**2
    norm_factor = norm_factor**0.5
    return vector/norm_factor

In [28]:
comp_encoded_lang_blocks_train = jobload('comp_encoded_lang_blocks_train.jbl')

HD_array = []
HD_array_keys = []
for key in comp_encoded_lang_blocks_train:
    HD_array_keys.append(key)
    HD_array.append(normalize_comp_vect(comp_encoded_lang_blocks_train[key]))
HD_array = np.array(HD_array)
HD_array = np.reshape(HD_array, [21, 1000])

In [120]:
def create_corr_hdv(vector):
    rea_ = np.dstack((vector.real, vector.imag))
    return rea_

In [123]:
real_HD_array = create_corr_hdv(HD_array)

In [38]:
test_keys = {
    'bg' : 'Bulgarian',
    'cs' : 'Czech',
    'da' : 'Danish',
    'de' : 'German',
    'el' : 'Greek',
    'en' : 'English',
    'et' : 'Estonian',
    'fi' : 'Finnish',
    'fr' : 'French',
    'hu' : 'Hungarian',
    'it' : 'Italian',
    'lv' : 'Latvian',
    'lt' : 'Lithuanian',
    'nl' : 'Dutch',
    'pl' : 'Polish',
    'pt' : 'Portuguese',
    'ro' : 'Romanian',
    'sk' : 'Slovak',
    'sl' : 'Slovene',
    'es' : 'Spanish',
    'sv' : 'Swedish'
}

In [39]:
test_data_root = 'comp_encoded_langs_test'
data_lang_paths = os.listdir(test_data_root)

In [40]:
lang_paths_test = defaultdict()
for path in data_lang_paths:
    lang_paths_test[path[:2]] = os.path.join(test_data_root, path)

In [160]:
lang_paths_test['bg']

'comp_encoded_langs_test\\bgcomp_encoded_test.jbl'

In [161]:
lang_blocks_nl = jobload(lang_paths_test['bg'])

(-1.6986166767466355-8.158853460151631j)

In [163]:
gt = []
prediction = []

for key in lang_paths_test.keys():
    true_lang = test_keys[key]
    lang_blocks = jobload(lang_paths_test[key])
    for tb in tqdm(range(len(lang_blocks))):
        test_block = lang_blocks[tb]
        gt.append(true_lang)
        test_block = normalize_comp_vect(test_block)
        pred_lang = HD_array_keys[comp_cos_sim(HD_array, test_block).argmax()]
        prediction.append(pred_lang)
    del lang_blocks

100%|██████████| 10000/10000 [00:02<00:00, 4438.91it/s]


In [37]:
#jobsave([gt, prediction], 'test_2_gt_results.jbl')

In [164]:
cnf_matrix = confusion_matrix(gt, prediction, labels=HD_array_keys)

In [165]:
plt.figure(figsize = (23, 17), dpi=500)
plot_confusion_matrix(cnf_matrix, classes=HD_array_keys,
                      title='T2:Compelex vectors experiment. Overall accuracy: {:.3f}'.format(
                          np.diag(cnf_matrix).sum() / cnf_matrix.sum()
                      ),
                      x_label='True language',
                      y_label='Predicted language'
                     );

Confusion matrix, without normalization
[[363864   2145    796   2236   5314    369   1734    993    627    873
    1363   2815   2667   3424   2928   1903   1348   2771   4534    336
    1220]
 [ 12004 459139   2103   2550  11177    864   2391    978   3242   1984
    1915   2627   4700   7028   4230   2224   2109  81979  37334   1174
    1584]
 [    18      7   8998     64     21     53     18     12    123     12
      36     20     20    197      3     16     42      4      6     25
     304]
 [    24     32     73   9300     23     78     38      6     69      4
      15     44     21    164     16     16     13      7      5     13
      39]
 [   100      5     17     14   9375      6     28     72     45     13
      24     32     52     98     38      9     21     11      2      4
       9]
 [    61     50    256    131     93   7852    148     45    275     49
     154     31    141    110     18     79    131     78     37    141
      80]
 [    59     21     59     60    140

In [166]:
t2_report = metrics.classification_report(gt, prediction, digits=3)

In [167]:
print(t2_report)

              precision    recall  f1-score   support

   Bulgarian      0.964     0.900     0.931    404260
       Czech      0.990     0.714     0.830    643336
      Danish      0.656     0.900     0.759      9999
       Dutch      0.421     0.885     0.570     10000
     English      0.795     0.788     0.792      9960
    Estonian      0.618     0.850     0.716      9999
     Finnish      0.760     0.918     0.832      9998
      French      0.579     0.891     0.702      9999
      German      0.605     0.930     0.733     10000
       Greek      0.344     0.940     0.504      9975
   Hungarian      0.722     0.862     0.786     10000
     Italian      0.658     0.899     0.760      9998
     Latvian      0.530     0.776     0.630      9999
  Lithuanian      0.467     0.819     0.595      9999
      Polish      0.528     0.898     0.665     10000
  Portuguese      0.631     0.907     0.744     10000
    Romanian      0.621     0.721     0.667      9960
      Slovak      0.068    

In [144]:
cnf_matrix = confusion_matrix(gt, prediction, labels=HD_array_keys)

In [145]:
plt.figure(figsize = (23, 17), dpi=500)
plot_confusion_matrix(cnf_matrix, classes=HD_array_keys,
                      title='T2:Compelex vectors experiment. Overall accuracy: {:.3f}'.format(
                          np.diag(cnf_matrix).sum() / cnf_matrix.sum()
                      ),
                      x_label='True language',
                      y_label='Predicted language'
                     );

Confusion matrix, without normalization
[[8059  191   68  159  134  119   66   44   53   88  109   79   78  113
   117   57   41   84  122   81   98]
 [ 217 6654   42   72  149   43   35   19   81   52   76   45   71  121
   142   31   36 1193  805   49   67]
 [  18    7 8998   64   21   53   18   12  123   12   36   20   20  197
     3   16   42    4    6   25  304]
 [  24   32   73 9300   23   78   38    6   69    4   15   44   21  164
    16   16   13    7    5   13   39]
 [ 100    5   17   14 9375    6   28   72   45   13   24   32   52   98
    38    9   21   11    2    4    9]
 [  61   50  256  131   93 7852  148   45  275   49  154   31  141  110
    18   79  131   78   37  141   80]
 [  59   21   59   60  140   49 8496  208  136   45   66   81   86  109
    44   35   62   27   21   98   97]
 [ 105   22   10   21   81   10  249 9179   22   27   18  115   41   40
    12    3    8    5   10    5   15]
 [  12   32   78   71   19   13   10    7 8908    6  134   21   42  155
     7  

In [146]:
t2_report = metrics.classification_report(gt, prediction, digits=3)

In [147]:
print(t2_report)

              precision    recall  f1-score   support

   Bulgarian      0.811     0.809     0.810      9960
       Czech      0.726     0.665     0.694     10000
      Danish      0.824     0.900     0.860      9999
       Dutch      0.819     0.885     0.851     10000
     English      0.891     0.788     0.837      9960
    Estonian      0.874     0.850     0.861      9999
     Finnish      0.903     0.918     0.910      9998
      French      0.764     0.891     0.823      9999
      German      0.859     0.930     0.893     10000
       Greek      0.851     0.940     0.893      9975
   Hungarian      0.934     0.862     0.897     10000
     Italian      0.851     0.899     0.874      9998
     Latvian      0.832     0.776     0.803      9999
  Lithuanian      0.794     0.819     0.806      9999
      Polish      0.887     0.898     0.893     10000
  Portuguese      0.877     0.907     0.892     10000
    Romanian      0.877     0.721     0.791      9960
      Slovak      0.741    

In [63]:
cnf_matrix = confusion_matrix(gt, prediction, labels=HD_array_keys)

In [68]:
plt.figure(figsize = (23, 17), dpi=500)
plot_confusion_matrix(cnf_matrix, classes=HD_array_keys,
                      title='T2:Compelex vectors experiment. Overall accuracy: {:.3f}'.format(
                          np.diag(cnf_matrix).sum() / cnf_matrix.sum()
                      ),
                      x_label='True language',
                      y_label='Predicted language'
                     );

Confusion matrix, without normalization
[[561  60  21  41  13  38   4  11  20  24  26  13  11  28  13   7   5  20
   19  25  40]
 [ 42 304  13  23   4  23   2   8  30  18  28   9   4  23  75   4   7  72
  253  28  30]
 [  0   1 916   4   4   4   3   0  11   0   4   3   2  18   0   1   1   0
    0   2  26]
 [  2   4   4 943   2   5   3   2   4   0   1   2   2  13   1   2   0   1
    1   2   6]
 [  8   2   1   1 937   0   2   6   6   1   2   4   8  15   3   0   2   0
    0   0   2]
 [ 11  18  88  55   9 442  56  17  73  12  35   6  16   9   1  20  11  35
   16  38  32]
 [ 16   9  22  21  19  28 519  83  38  15  19  12  10  37  22  13   7   6
    6  55  43]
 [ 14   1   2   4   8   0  19 926   0   3   1  10   4   0   2   0   2   0
    0   0   3]
 [  2   4   7   1   2   2   0   1 924   0   5   0   6  12   0   2   2   2
    2  25   1]
 [  9   2  14  20  16  24  13  11  33 549  34  36  47  20  10   7   5   7
   64  64  15]
 [  1   1   1   2   1   0   0   2  30   0 913   1   3   6   0   8   1 

In [69]:
t2_report = metrics.classification_report(gt, prediction, digits=3)

In [70]:
print(t2_report)

              precision    recall  f1-score   support

   Bulgarian      0.669     0.561     0.610      1000
       Czech      0.477     0.304     0.371      1000
      Danish      0.708     0.916     0.799      1000
       Dutch      0.711     0.890     0.790      1000
     English      0.604     0.442     0.510      1000
    Estonian      0.747     0.519     0.612      1000
     Finnish      0.796     0.927     0.856       999
      French      0.598     0.924     0.726      1000
      German      0.694     0.943     0.799      1000
       Greek      0.840     0.937     0.886      1000
   Hungarian      0.726     0.549     0.625      1000
     Italian      0.712     0.913     0.800      1000
     Latvian      0.662     0.414     0.510      1000
  Lithuanian      0.622     0.487     0.546      1000
      Polish      0.587     0.644     0.614      1000
  Portuguese      0.778     0.923     0.844      1000
    Romanian      0.748     0.288     0.416      1000
      Slovak      0.485    

In [49]:
test_keys = {
    'bul' : 'Bulgarian',
    'ces' : 'Czech',
    'dan' : 'Danish',
    'deu' : 'German',
    'ell' : 'Greek',
    'eng' : 'English',
    'est' : 'Estonian',
    'fin' : 'Finnish',
    'fra' : 'French',
    'hun' : 'Hungarian',
    'ita' : 'Italian',
    'lav' : 'Latvian',
    'lit' : 'Lithuanian',
    'nld' : 'Dutch',
    'pol' : 'Polish',
    'por' : 'Portuguese',
    'ron' : 'Romanian',
    'slk' : 'Slovak',
    'slv' : 'Slovene',
    'spa' : 'Spanish',
    'swe' : 'Swedish'
}

13102

In [50]:
train_keys = {
    'bul' : 'Bulgarian',
    'ces' : 'Czech',
    'dan' : 'Danish',
    'deu' : 'German',
    'ell' : 'Greek',
    'eng' : 'English',
    'est' : 'Estonian',
    'fin' : 'Finnish',
    'fra' : 'French',
    'hun' : 'Hungarian',
    'ita' : 'Italian',
    'lav' : 'Latvian',
    'lit' : 'Lithuanian',
    'nld' : 'Dutch',
    'pol' : 'Polish',
    'por' : 'Portuguese',
    'ron' : 'Romanian',
    'slk' : 'Slovak',
    'slv' : 'Slovene',
    'spa' : 'Spanish',
    'swe' : 'Swedish'
}

404260

In [77]:
test_range = np.linspace(-1, 1, 20001)

In [92]:
a = test_range[2]
b = img_counterpart(a)
(a**2 + b**2)**0.5 

1.0

In [64]:
import cmath

In [79]:
len(test_range)

20001

In [89]:
def img_counterpart(real):
    img_pos = (1- real**2)**0.5
    
    return img_pos

In [90]:
img_counterpart(0.12)

0.9927738916792685

In [115]:
HD_array_keys[0]

'Bulgarian'

In [119]:
pred_lang = HD_array_keys[cosine_similarity([nor_lang_train['Bulgarian'][0]], test_block).argmax()]

ValueError: could not convert string to float: 'e'